Support Vector Machine 은 support vectors 와 경계면의 모습을 살펴보는 것이 중요하기 때문에 2 차원의 인공데이터를 생성하여 이를 통해 Support Vector Classifer 와 Support Vector Regression 의 사용법을 익혀봅니다. 데이터의 생성함수와 각 클래스의 영역을 표시하는 함수는 모두 svm_utils.py 에 미리 만들어 두었습니다.

In [1]:
import numpy as np
from bokeh.plotting import show, output_notebook, save

from svm_utils import generate_svc_data
from svm_utils import generate_svr_data
from svm_utils import scatterplot_2class
from svm_utils import draw_activate_image
from svm_utils import append_rbf_radial_basis
from svm_utils import scatterplot_timeseries
from svm_utils import net_parameter_compression_ratio


output_notebook()

Loading BokehJS ...

`generate_svc_data()` 함수는 linear inseparable dataset 을 만드는 함수입니다.

In [2]:
# linear inseparable dataset
X, label = generate_svc_data(n_data=50, p_noise=0.0)
sv_dummy = sv=np.ones(X.shape[0], dtype=np.int)

show(scatterplot_2class(X, label, sv_dummy, size=5, height=400, width=400))

세 개의 점을 제거하여 linear separable case 로 만들어둡니다.

In [3]:
# linear separable dataset
subindices = np.array([i for i in range(50) if not i in [8, 13, 14]])
X_ = X[subindices]
label_ = label[subindices]
sv_dummy = np.ones(X_.shape[0])

show(scatterplot_2class(X_, label_, sv_dummy, size=5, height=400, width=400))

`X_` 는 linear separable dataset 이니 linear kernel SVM classifier 를 학습해 봅니다. 본래 SVM 은 classification probability 를 제공하지 않습니다. 하지만 predict 의 결과를 확률적으로 이해하고 싶을 때는 SVM 의 `probability` 를 True 로 설정해둡니다.

In [4]:
from sklearn.svm import SVC

C = 10.0
svm = SVC(
    C=C,
    kernel='linear',         # linear SVM 을 학습합니다. 
    gamma='auto_deprecated', # gamma 는 RBF kernel 을 이용할 때 설정합니다.
    coef0=0.0,               # ceof0 은 polynomial kernel 을 이용할 때 설정합니다.
    class_weight='balanced', # imbalanced classes 의 경우에는 클래스 개수의 역수로 가중치를 부여합니다.
    decision_function_shape='ovr', # multi-classes classification 의 경우 one-verses-rest 를 합니다.
                             # 다른 옵션으로는 'ovo', one-verses-one 을 이용할 수 있습니다.
    probability=True,        # decision value 를 이용하여 확률 추정값을 계산합니다.
    shrinking=False)

svm.fit(X_, label_)

SVC(C=10.0, cache_size=200, class_weight='balanced', coef0=0.0,
    decision_function_shape='ovr', degree=3, gamma='auto_deprecated',
    kernel='linear', max_iter=-1, probability=True, random_state=None,
    shrinking=False, tol=0.001, verbose=False)

scikit learn 의 SM 들은 decision function 을 제공합니다. f(q) 의 값을 return 합니다.

In [5]:
decision = svm.decision_function(X_)

print(f'Shape of decision = {decision.shape}')
print(f'Sample of decsion\n{decision[:5]}')

Shape of decision = (47,)
Sample of decsion
[-0.88010687  0.58182229 -0.770488   -2.57828079  2.98934483]


`predict()` 함수는 decision score 를 바탕을 f(q) > 0 이면 1 로 분류합니다.

In [6]:
print('sample of predict')
svm.predict(X_)[:5]

sample of predict


array([0, 1, 0, 0, 1])

앞서 `SVC(probability=True)` 로 설정하였기 때문에 분류 확률 값을 얻을 수 있습니다.

In [7]:
print('sample of predict_proba')
svm.predict_proba(X_)[:3]

sample of predict_proba


array([[0.76791385, 0.23208615],
       [0.18652353, 0.81347647],
       [0.7303586 , 0.2696414 ]])

Support vectors index 는 `support_` 에, alpha 는 `dual_coef_` 에 저장되어 있습니다.

In [8]:
print(f'Indices of support vector, shape = {svm.support_.shape}')
print(svm.support_)

print(f'\nDual coefficient (alpha) of support vectors, shape = {svm.dual_coef_.shape}')
print(svm.dual_coef_)

ratio = svm.support_.shape[0] / X_.shape[0]
print(f'\nRatio of support vectors = {ratio:.4}')

Indices of support vector, shape = (11,)
[ 0  2 46  1 12 13 16 23 28 43 45]

Dual coefficient (alpha) of support vectors, shape = (1, 11)
[[-16.78571429 -16.78571429 -16.78571429   7.12121212   7.12121212
    7.12121212   6.3601867    7.12121212   7.12121212   7.12121212
    1.26968343]]

Ratio of support vectors = 0.234


Linear kernel SVM 에 대하여 wx + b 라는 식을 학습할 수 있습니다. w 와 b 가 각각 `coef_` 와 `intercept_` 에 저장되어 있습니다.

In [9]:
print('Coefficient of linear SVM hyperplane\n')
print(f'coef = {svm.coef_}')
print(f'intercept = f{svm.intercept_}')

line = ' + '.join([f'{svm.coef_[0][i]:.4} * x{i+1}' for i in range(X.shape[1])])
line += f' + {svm.intercept_[0]:.4}'
print(f'\nhyperplane = {line}')

Coefficient of linear SVM hyperplane

coef = [[ 3.29834496 -7.53926743]]
intercept = f[2.70172077]

hyperplane = 3.298 * x1 + -7.539 * x2 + 2.702


Margin 은 1/|w|_2 였습니다.

In [10]:
# margin = 1 / |w|_2
margin = 1 / np.sqrt(np.sum(svm.coef_ ** 2))
margin

0.12151858459938729

그림을 그릴 때 어떤 점이 support vector 인지, 그리고 각점의 decision score 가 얼마인지의 정보가 필요합니다. 이를 계산하는 과정을 미리 함수로 만들어 둡니다.

In [11]:
def prepare_plot_resource(model, X):
    sv = np.zeros(X.shape[0], dtype=np.int)
    sv[model.support_] = 1
    decision = svm.decision_function(X)
    return sv, decision

미리 만들어둔 함수를 이용하여 각 클래스의 영역을 decision score 를 바탕으로 계산하여 그림을 그려봅니다.

In [12]:
sv, decision = prepare_plot_resource(svm, X_)

title = f'Linear SVM with C={C}'
p = draw_activate_image(svm, X_, resolution=500, decision=True, title=title)
p = scatterplot_2class(X_, label_, sv, decision, p=p, size=10)
show(p)

서로 다른 C 를 적용하여 margin 과 support vectors 가 변하는 모습을 관찰해 봅니다. Regularization cost 가 줄어들자 더 넓은 margin 과 더 많은 support vectors 가 선택됩니다. -1 < decision score < 1 에 위치한 support vectors 는 epsilon > 0 인 점들입니다.

In [13]:
from bokeh.layouts import gridplot

figures = []
for C in [1.0, 5.0, 20.0]:
    svm = SVC(C=C, kernel='linear')
    svm.fit(X_, label_)
    sv, decision = prepare_plot_resource(svm, X_)
    ratio = svm.support_.shape[0] / X.shape[0]
    title = f'Linear SVM with C={C}, |SV|={ratio:.4}'
    p = draw_activate_image(svm, X_, resolution=500, decision=True, title=title, height=400, width=400)
    p = scatterplot_2class(X_, label_, sv, decision, p=p, size=10)
    figures.append(p)

gp_linsvm = gridplot([figures])
show(gp_linsvm)

RBF kernel 을 이용하면 non-linear hyper plane 을 얻을 수 있습니다. 이 역시 C 와 gamma 를 조절하며 margin 과 support vectors 의 변화를 살펴봅니다.

In [14]:
grid = []
for C in [1.0, 10.0, 100.0]:
    figures = []
    for gamma in [5.0, 30.0, 100.0]:
        svm = SVC(C=C, kernel='rbf', gamma=gamma)
        svm.fit(X, label)
        sv, decision = prepare_plot_resource(svm, X)
        ratio = svm.support_.shape[0] / X.shape[0]
        title = f'RBF SVM C={C}, gamma={gamma}, |SV|={ratio:.4}'
        p = draw_activate_image(svm, X, resolution=500, decision=True, title=title, height=400, width=400)
        p = scatterplot_2class(X, label, sv, decision, size=10, p=p)
        figures.append(p)
    grid.append(figures)
gp_rbf = gridplot(grid)
show(gp_rbf)

미리 만들어둔 함수를 이용하여 exp(-gamma(|xi - xj|^2) 의 값이 0.05 보다 큰 지점들에 원을 그려 각 radial basis 들의 영역을 살펴봅니다.

In [15]:
C, gamma = 100, 45
svm = SVC(C=C, kernel='rbf', gamma=gamma)
svm.fit(X, label)

sv, decision = prepare_plot_resource(svm, X)
ratio = svm.support_.shape[0] / X.shape[0]
title = f'RBF SVM C={C}, gamma={gamma}, |SV|={ratio:.4} + RBF basis'

p_rbf_basis = draw_activate_image(svm, X, resolution=500, decision=True, alpha=0.2, title=title)
p_rbf_basis = append_rbf_radial_basis(svm, X, label, gamma, p=p_rbf_basis, circle_alpha=0.1)
p_rbf_basis = scatterplot_2class(X, label, sv, decision, size=10, p=p_rbf_basis)
show(p_rbf_basis)

Regression 용 데이터를 생성합니다.

In [16]:
x_line, x, y_line, y = generate_svr_data(n_data=200, n_repeats=5)
X_line = x_line.reshape(-1,1)
X = x.reshape(-1,1)

p_tdata = scatterplot_timeseries(x, y, y_line, title='Dataset')

SVR 은 SVM 과 epsilon tube 를 설정하는 부분을 제외하면 모두 동일합니다. 이 역시 하이퍼 패러매터를 조절하며 경향이 달라지는 점을 살펴봅니다.

In [17]:
from sklearn.svm import SVR

grid = []
for gamma in [1.0, 5.0, 10.0]:
    figures = []
    for epsilon in [0.5, 2.0, 5.0]:
        
        svr = SVR(kernel='rbf', gamma=gamma, C=50, epsilon=epsilon)
        svr.fit(X, y)
        y_pred = svr.predict(X_line)

        ratio = svr.support_.shape[0] / X.shape[0]
        title = f'SVR gamma={gamma}, epsilon={epsilon}, C=50, |SV|={ratio:.4}'

        n_data = X.shape[0]
        dummy_label = np.zeros(n_data, dtype=np.int)
        sv = np.zeros(n_data, dtype=np.int)
        sv[svr.support_] = 1
        coef = np.zeros(n_data)
        coef[svr.support_] = svr.dual_coef_.reshape(-1)

        p = scatterplot_timeseries(x, y, y_line, size=1, height=400, width=600, title=title)
        p = scatterplot_2class(np.vstack([x, y]).T, dummy_label, sv, coef, size=3, p=p)
        p = scatterplot_timeseries(x_line, y_pred, y_pred, size=3, point_color='#d7191c', line_color='#d7191c', p=p)

        figures.append(p)
    grid.append(figures)
gp_svr = gridplot(grid)
show(gp_svr)

In [18]:
from sklearn.linear_model import Ridge
from sklearn.neural_network import MLPRegressor

# SVR
svr = SVR(kernel='rbf', gamma=10.0, C=50, epsilon=2.0)
svr.fit(X, y)
y_pred_svr = svr.predict(X_line)

ratio = svr.support_.shape[0] / X.shape[0]
title_svr = f'SVR gamma=10.0, epsilon=2.0, C=50, |SV|={ratio:.4}'

# Ridge regression
ridge = Ridge(alpha=0.1)
ridge.fit(X, y)
y_pred_ridge = ridge.predict(X_line)
title_ridge = f'Ridge regression'

# Feed-forward network
np.random.seed(1)
mlp = MLPRegressor(hidden_layer_sizes=(50, 50, 50), solver='adam', activation='tanh', max_iter=1000)
mlp.fit(X, y)
y_pred_mlp0 = mlp.predict(X_line)
times = net_parameter_compression_ratio(mlp, X)
title_mlp0 = f'MLP h=(50,50,50), adam, tanh, #parameter = x {times:.4}'

# Feed-forward network
np.random.seed(1)
mlp = MLPRegressor(hidden_layer_sizes=(200, 5), solver='adam', activation='tanh', max_iter=1000)
mlp.fit(X, y)
y_pred_mlp1 = mlp.predict(X_line)
times = net_parameter_compression_ratio(mlp, X)
title_mlp1 = f'MLP h=(200,5), adam, tanh, #parameter = x {times:.4}'

titles = [title_svr, title_ridge, title_mlp0, title_mlp1]
preds = [y_pred_svr, y_pred_ridge, y_pred_mlp0, y_pred_mlp1]

figures = []
for title, y_pred in zip(titles, preds):
    p = scatterplot_timeseries(x, y, y_line, title=title, height=400, width=600)
    p = scatterplot_timeseries(x_line, y_pred, y_pred, size=4, point_color='#d7191c', line_color='#d7191c', p=p)
    figures.append(p)
gp_regression_compare = gridplot([figures[:2], figures[2:]])
show(gp_regression_compare)

In [19]:
from sklearn.neighbors import KNeighborsRegressor

knn = KNeighborsRegressor(n_neighbors=50)
knn.fit(X, y)
y_pred_knn = knn.predict(X_line)
title_knn = f'k-NN regressor, n_neighbors=50'
p_knn = scatterplot_timeseries(x, y, y_line, title=title_knn, height=400, width=600)
p_knn = scatterplot_timeseries(x_line, y_pred_knn, y_pred_knn, size=4, point_color='#d7191c', line_color='#d7191c', p=p_knn)
show(p_knn)

In [20]:
# save(gp_linsvm, './figures/svm_linear_various_parameters.html')
# save(gp_rbf, './figures/svm_rbf_various_parameters.html')
# save(p_rbf_basis, './figures/svm_rbf_basis.html')
# save(gp_svr, './figures/svr_various_parameters.html')
# save(gp_regression_compare, './figures/regression_comparison.html')
# save(p_knn, './figures/regression_comparison_knn.html')